In [ ]:
import pandas as pd
from pandas.core.dtypes.common import is_datetime64_any_dtype

vessel_positions = pd.read_csv('data/vessel_positions.csv')
vessel_characteristics = pd.read_csv('data/vessel_characteristics.csv')

In [2]:
'''
Convert a column that mixes Excel-serial numbers and “DD/MM/YYYY HH:MM” strings into one UTC-timestamp Series.
Rounds timings to the nearest second.

Returns unchanged if the column is already a datatime dtype. Otherwise, returns a Series of dtype datetime64[ns, UTC]; unparseable rows become NaT.
'''

def to_timestamp(dataframe, column_name):

    s = dataframe[column_name]

    if is_datetime64_any_dtype(s):
        return s

    numbers = pd.to_numeric(s, errors="coerce") # floats where possible, NaN otherwise
    dt1 = pd.to_datetime(numbers, unit="D", origin="1899-12-30", utc=True) # convert floats to timestamps

    dates = s[numbers.isna()] # take the non-numeric rows

    # convert dates to timestamps
    dt2 = pd.to_datetime(dates, format="%d/%m/%Y %H:%M", dayfirst=True, utc=True, errors="coerce")

    final_column = dt1.fillna(dt2) # merge dt1 and dt2 into a single series of timestamps

    # round the timings to the nearest second
    final_column = final_column.dt.round('s')

    return final_column

The to_timestamp function is used convert datetime columns of string objects to datetime64[ns, UTC] dtype. This data type conversion provides accurate comparisons, date arithmetic, timezone handling, faster operations, less storage, and cleaner/built-in support (pandas and other libraries).

Four additional functions, object_to_string, float_to_Int64, std_to_boolean, and to_date, were implemented to convert columns from the default data types to the data types that suit the contents of each column best.

The strip_html function is used to clean axs_notes_dry column from <br> html elements.

All columns which were mistakenly altered to have the boolean data type because they were empty were adjusted back to the most suitable data type.

In [3]:
'''
Takes a dataframe, searches for text columns of object dtype and converts them to the string dtype.
Returns the modified dataframe.
'''

def object_to_string(dataframe):

    obj_cols = dataframe.select_dtypes(include=["object"]).columns

    for column in obj_cols:
        if all(isinstance(v, str) for v in dataframe[column].dropna()):
            dataframe[column] = dataframe[column].astype("string")

    return dataframe

In [4]:
'''
Takes a dataframe, searches for integer-like columns of float dtype and converts them to Pandas' Int64 dtype.
Returns the modified dataframe.
'''

def float_to_Int64(dataframe):

    float_cols = dataframe.select_dtypes(include=["float"]).columns

    for column in float_cols:
        if np.isclose(dataframe[column].dropna() % 1, 0).all():
            dataframe[column] = dataframe[column].astype("Int64")

    return dataframe

In [5]:
'''
Takes a dataframe, searches for columns of the integer data type that are boolean in nature and converts them to boolean dtype.
Standardizes boolean columns from 'Y'/'N' to True/False
Returns the modified dataframe.
'''

def std_to_boolean(dataframe):
    int_cols = dataframe.select_dtypes(include=["integer"]).columns

    for column in int_cols:
        if dataframe[column].dropna().isin([0, 1]).all():
            dataframe[column] = dataframe[column].astype("boolean")

    str_cols = dataframe.select_dtypes(include=["string"]).columns

    for column in str_cols:
        # Standardise to upper-case and strip whitespace once
        col_std = dataframe[column].dropna().str.strip().str.upper()

        if col_std.isin(["Y", "N"]).all():
            dataframe[column] = (
                dataframe[column].str.strip()
                   .str.upper()
                   .map({"Y": True, "N": False})
                   .astype("boolean")
            )

    return dataframe

In [6]:
'''
Takes a dataframe column of dates, converts it from object dtype to datetime dtype.
 Returns the modified column.
'''

def to_date(column):

    patterns = ["%d/%m/%Y", "%Y-%m-%d"]

    parsed = pd.Series(pd.NaT, index=column.index) # start all NaT

    for fmt in patterns:
        mask = parsed.isna() # rows still unparsed
        parsed.loc[mask] = pd.to_datetime(
            column.loc[mask],
            format=fmt,
            dayfirst=(fmt == "%d/%m/%Y"),
            errors="coerce"
        )

    return parsed

In [7]:
'''
Takes a dataframe column.
Removes <br>, <br/>, <br /> (case-insensitive) and collapse multiple spaces.
Returns the modified column.
'''

import pandas as pd
import re

def strip_html(column):
    return (
           column.str.replace(r"<br\s*/?>", " ", regex=True, flags=re.I)
           .str.replace(r"\s+", " ", regex=True)
           .str.strip()
    )

In [8]:
# vessel_positions data cleaning

# Convert datetime columns of string objects to datetime64[ns, UTC] dtype

datetime_cols = ['zone_entry_time', 'zone_out_time', 'port_entry_time',
        'port_out_time', 'operation_location_entry_time', 'operation_location_out_time',
        'waiting_zone_entry_time', 'waiting_zone_out_time', 'ais_eta', 'last_seen']

for col in datetime_cols:
    vessel_positions[col] = to_timestamp(vessel_positions, col)

date_cols = ['status_date_time', 'updated_at']

for col in date_cols:
    vessel_positions[col] = pd.to_datetime(vessel_positions[col], format="%d/%m/%Y", dayfirst=True, errors="coerce")

# Convert boolean in nature columns from integer dtype to boolean dtype
std_to_boolean(vessel_positions)

# Convert text columns from object dtype to string dtype
object_to_string(vessel_positions)

# Convert integer-like float columns to Int64
float_to_Int64(vessel_positions)

index      imo  vessel_dwt status_date_time  in_blackout  ais_speed  \
0          0  1014149       11717       2024-08-20        False        0.0   
1          1  1014163       39815       2024-08-20        False        0.0   
2          2  1014199       11722       2024-08-20        False        0.0   
3          3  1014254       13465       2024-08-20        False       11.8   
4          4  1014591       39415       2024-08-20        False       11.0   
...      ...      ...         ...              ...          ...        ...   
71630  71630  9978573      210870       2024-08-24        False        0.0   
71631  71631  9980174      181283       2024-08-24        False        8.0   
71632  71632  9980186      181283       2024-08-24        False       11.0   
71633  71633  9983578      182498       2024-08-24        False        0.0   
71634  71634  9989730      182316       2024-08-24        False       11.0   

       ais_draft  vessel_speed_ratio  ais_lat  ais_long  ...  \
0            5.1                 NaN  34.3504  133.8770  ...   
1            6.1                 NaN -33.8022  137.0520  ...   
2            4.4                 NaN  34.4042  133.4250  ...   
3            9.5                 NaN  11.7398  109.4890  ...   
4           10.6                 NaN  16.4267  113.8580  ...   
...          ...                 ...      ...       ...  ...   
71630        3.5                 NaN  34.4930  133.7310  ...   
71631       18.0                 NaN -31.5604   34.9163  ...   
71632       18.3                 NaN   2.0483  104.8680  ...   
71633        9.0                 NaN -21.2435  149.3020  ...   
71634       17.2                 NaN   6.8133   98.3317  ...   

      real_destination_country_name  real_destination_zone_id  \
0                             Japan                        73   
1                             China                        73   
2                             Japan                        73   
3                             Japan                        73   
4                              <NA>                      <NA>   
...                             ...                       ...   
71630                         Japan                        73   
71631                         Japan                        73   
71632                         China                        73   
71633                          <NA>                      <NA>   
71634                         India                        71   

      real_destination_zone_name vessel_operational_status  \
0                       Far East              waiting_load   
1                       Far East              at_port_load   
2                       Far East              waiting_load   
3                       Far East              at_sea_laden   
4                           <NA>              at_sea_laden   
...                          ...                       ...   
71630                   Far East       at_port_discharging   
71631                   Far East              at_sea_laden   
71632                   Far East              at_sea_laden   
71633                       <NA>              at_port_load   
71634           East Coast India              at_sea_laden   

      vessel_commodity_onboard vessel_commodity_group_onboard  \
0                         <NA>                           <NA>   
1                        Grain                          Grain   
2                         <NA>                           <NA>   
3                       Steels                         Steels   
4                       Steels                         Steels   
...                        ...                            ...   
71630                 Iron Ore                       Iron Ore   
71631                 Iron Ore                       Iron Ore   
71632                 Iron Ore                       Iron Ore   
71633              Coking Coal                           Coal   
71634              Coking Coal                           Coa

In [9]:
# vessel_characteristics data cleaning

# Convert datetime columns of string objects to datetime64[ns, UTC] dtype

datetime_cols = ['update_date']

for col in datetime_cols:
    vessel_characteristics[col] = to_timestamp(vessel_characteristics, col)

date_cols = ['built', 'demolition_date', 'keel_laying_date', 'launching_date', 'reported_date', 'cancelled_date', 'last_dd_date', 'next_dd_date', 'last_ss_date', 'next_ss_date', 'conversion_date']

for col in date_cols:
    vessel_characteristics[col] = to_date(vessel_characteristics[col])

# Convert text columns from object dtype to string dtype
object_to_string(vessel_characteristics)

# Convert integer-like float columns to Int64
float_to_Int64(vessel_characteristics)

# Convert boolean in nature columns from integer dtype to boolean dtype
# Separate open_hatches into categorical and boolean columns first

type_map = {
    "BOX":  "BOX",
    "OHBS": "OHBS",
    "Y":    "generic",
    "N":    "none"
}
vessel_characteristics["open_hatches"] = (
    vessel_characteristics["open_hatches"].map(type_map)
       .astype("category")
)

bool_map = {"BOX": True, "OHBS": True, "generic": True, "none": False}
bool_series = (
    vessel_characteristics["open_hatches"]
      .map(bool_map)
      .astype("boolean")
)

pos = vessel_characteristics.columns.get_loc("open_hatches")

vessel_characteristics.insert(
    loc=pos + 1,
    column="open_hatches_bool",
    value=bool_series
)

std_to_boolean(vessel_characteristics)

# return empty column to original dtype (or delete them)

vessel_characteristics["technical_manager"].astype("string")
vessel_characteristics["parent_shipowner"].astype("string")
vessel_characteristics["doc_holder"].astype("string")
vessel_characteristics["crew_manager"].astype("string")
vessel_characteristics["ism_manager"].astype("string")
vessel_characteristics["technical_manager_id"].astype("Int64")
vessel_characteristics["technical_manager_flag"].astype("string")
vessel_characteristics["technical_manager_flag_id"].astype("Int64")
vessel_characteristics["parent_shipowner_id"].astype("Int64")
vessel_characteristics["parent_shipowner_flag"].astype("string")
vessel_characteristics["parent_shipowner_flag_id"].astype("Int64")
vessel_characteristics["doc_holder_id"].astype("Int64")
vessel_characteristics["doc_holder_flag"].astype("string")
vessel_characteristics["doc_holder_flag_id"].astype("Int64")
vessel_characteristics["crew_manager_id"].astype("Int64")
vessel_characteristics["crew_manager_flag"].astype("string")
vessel_characteristics["crew_manager_flag_id"].astype("Int64")
vessel_characteristics["ism_manager_id"].astype("Int64")
vessel_characteristics["ism_manager_flag"].astype("string")
vessel_characteristics["ism_manager_flag_id"].astype("Int64")
vessel_characteristics["cranes_position"].astype("string")
vessel_characteristics["private_comments"].astype("string")
vessel_characteristics["private_tags"].astype("string")
vessel_characteristics["private_notes"].astype("string")

# strip the html tags from axs_notes_dry

vessel_characteristics["axs_notes_dry"] = strip_html(vessel_characteristics["axs_notes_dry"])

In [30]:
# Initial exploratory analysis

import plotly.express as px

sub_df = vessel_positions[['vessel_operational_status', 'ais_speed', 'ais_draft']].dropna()

display(sub_df.describe())

fig = px.scatter(
    sub_df,
    x='ais_draft',
    y='ais_speed',
    color='vessel_operational_status',
    opacity=0.55,
    labels={'ais_draft':"Draft [m]", 'ais_speed':"Speed over ground [kt]",
            'vessel_operational_status':"Operational status"},
    title="Speed vs Draft coloured by vessel operational status",
    hover_data=sub_df.columns
)
fig.update_traces(marker=dict(line=dict(width=0.4, color="white")))
fig.update_layout(legend=dict(itemsizing="constant", title=None,
                              orientation="v", yanchor="top", y=0.99))
fig.show()

fig_facet = px.scatter(
    sub_df,
    x='ais_draft',
    y='ais_speed',
    color='vessel_operational_status',
    facet_col='vessel_operational_status', facet_col_wrap=3,    # 3 panels per row ⇒ 5 rows for 14 cats
    opacity=0.55,
    labels={'ais_draft':"Draft [m]", 'ais_speed':"Speed over ground [kt]"},
    title="Speed–Draft relationship per operational status"
)
# wipe every subplot’s y-axis title
fig_facet.update_yaxes(title_text="")

fig_facet.layout.yaxis.title.text = "Speed over ground [kt]"

fig_facet.for_each_annotation(
    lambda a: a.update(text=a.text.split("=")[-1].replace("_"," "))
)

fig_facet.update_traces(marker=dict(line=dict(width=0.4, color="white")))
fig_facet.show()

ais_speed     ais_draft
count  71581.000000  71581.000000
mean       6.061752      9.761255
std        6.415313      3.408483
min        0.000000      0.000000
25%        0.000000      7.100000
50%        8.000000      9.200000
75%       11.200000     12.000000
max      102.300000     25.500000

ais_speed is highly skewed: the median vessel moves at ≈ 8 kt while the mean is only 6 kt, pulled down by many “zero-speed” records. Extreme outliers reach 102 kt and almost certainly represent bad or mis-keyed AIS messages that should be excluded in further cleaning.

Draft (ais_draft) is more symmetric (median ≈ 9 m, IQR ≈ 7–12 m) but still shows occasional impossible zeros and a long tail up to 25.5 m.

The colour-coded scatter reveals three clear behavioural bands:

- At-sea laden vessels cluster around drafts 15–22 m and speeds 10–15 kt.
- At-sea ballast transits occupy shallow drafts 4–8 m with markedly higher speed variance.
- Port/anchorage/shipyard states concentrate near 0–2 kt regardless of draft, showing that speed is driven mostly by the activity rather than the loading condition in those modes.

In [35]:
import pandas as pd
import numpy as np

bins    = [0, 40_000, 60_000, 100_000, np.inf]
labels  = ["Handymax", "Supramax", "Panamax", "Capesize"]

vessel_class = pd.cut(
    vessel_characteristics["dwt"],
    bins=bins,
    labels=labels,
    right=False,
    ordered=True
)

pos = vessel_characteristics.columns.get_loc("dwt")

vessel_characteristics.insert(
    loc=pos + 1,
    column="vessel_class",
    value= vessel_class
)

vessel_characteristics['vessel_class'].count()

In [51]:
print("The number of vessels in each category is as follows:")
print(vessel_characteristics['vessel_class'].value_counts())

import plotly.express as px

counts = (
    vessel_characteristics["vessel_class"]
      .value_counts(dropna=True)
      .sort_index()
)

fig = px.pie(
    values=counts.values,
    names=counts.index,
    title="Number of unique vessels per class.",
)

fig.update_traces(textposition="inside",
                  texttemplate="%{percent:.1%}<br>%{value:,d}")
fig.show()

The number of vessels in each category is as follows:
vessel_class
Panamax     5668
Handymax    3976
Supramax    2918
Capesize    2195
Name: count, dtype: int64
